# Demonstration for Comparing the MSIS model versions in GEODYN

This notebook shows GODYN II output for using with the three versions of the MSIS models for thermospheric density: MSIS_86, MSIS_00, and MSIS_2.0.


The run parameters for the GEODYN run demoed here are:
```
 - Satellite:             Starlette
 - Observation Datatype:  SLR
 - Gen. Accelerations:    Off
 - Density Model:         NRLMSISe86, NRLMSISe00, MSIS 2.0
```


The arcs that are plotted are as follows:

     - Arc 1 --------  14 days ------ 03/09/14 - 03/##/##
     - Arc 2 --------  14 days ------ 03/09/28 - 03/##/##
     - Arc 3 --------  14 days ------ 03/10/12 - 03/##/##
     - Arc 4 --------  14 days ------ 03/10/26 - 03/##/##
     - Arc 5 --------  14 days ------ 03/11/09 - 03/##/##
     - Arc 6 --------  14 days ------ 03/11/23 - 03/##/##
     - Arc 7 --------  14 days ------ 03/12/07 - 03/##/##
     - Arc 8 --------  14 days ------ 03/12/21 - 03/##/##



### Load the simulation for a single model over all arcs

In [1]:
import numpy as np
import pandas as pd
from datetime import datetime,timedelta
import os.path
import linecache
from sys import exit
import os
import datetime


def Read_GEODYN_func_MultipleArcs(geodyn_run_params):
    '''
    This function acts as an intermediary to call to the 
    primary functions that call the GEODYN Output.
    '''
 

    #fix naming convention to be downstream functions
    if geodyn_run_params['sat_file'] == 'st':
        sat_name = 'starlette'

        
        
    #Inititalize that we will save out data along each arc in arc list   
    SatMain_AdjustedParams_arcs = {}
    trajectory_df_arcs = {}
    den_arcs = {}
    resids_observed_arcs = {}
    resids_summary_station_arcs = {}
    resids_meas_summary_arcs = {}
    RunStats_arcs = {}
    
    # Using the input params, construct the filenames for this arc:
    for arc in geodyn_run_params['arc_list']:
        
        file_name =  geodyn_run_params['sat_file'] + arc + '.'+ geodyn_run_params['grav_id']
        print('              Loading ', geodyn_run_params['path_to_data'] ,file_name,'\n' ,sep = '')


        
        
        
        # First check if the arc data exists in the place you think it does.
        iieout_file  = geodyn_run_params['path_to_data'] + 'IIEOUT/'+ file_name
        ascii_xyz_file = geodyn_run_params['path_to_data'] + 'XYZ_TRAJ/'+ file_name
        density_file = geodyn_run_params['path_to_data'] + 'DENSITY/'+ file_name

        
        
        
        # Do some pretty printing if it is wanted:
        if geodyn_run_params['verbose_loading'] == True:
            if os.path.isfile(iieout_file) == True:
                print('       File exists: iieout \n              ',iieout_file)
            else:
                print('ERROR: Not the correct path for file: iieout\n',iieout_file )
                exit(1)
            if os.path.isfile(ascii_xyz_file) == True:
                print('       File exists: ascii_xyz \n              ',ascii_xyz_file)
            else:
                print('ERROR: Not the correct path for file: ascii_xyz\n',ascii_xyz_file )
                exit(1)
            if os.path.isfile(density_file) == True:
                print('       File exists: densityfil \n              ',density_file)
            else:
                print('ERROR: Not the correct path for file: densityfil\n',density_file )
                exit(1)
        else:
            print(' ')
        if geodyn_run_params['verbose_loading'] == True:
            print('\n       Loading data... \n')
        else:
            pass

        
        
        
        
        
        # ######################################
        # ##    Read Adjusted Parameters      
        # ######################################
        import sys  
        sys.path.insert(0, '/data/geodyn_proj/analysis/util_funcs/py_read_geodyn_output/')
        from b_ReadGEODYN import Save_AdjustedParameters_geodyn
        
        SatMain_AdjustedParams_arcs[arc] = Save_AdjustedParameters_geodyn(geodyn_run_params['SAT_ID'], 
                                                                iieout_file, 
                                                                geodyn_run_params['AccelStatus'], 
                                                                geodyn_run_params['DATA_TYPE'])
        if geodyn_run_params['verbose_loading'] == True:
            print('       Parameter adjustment data loaded')
        else:
            pass



        # #####################################
        # #        Read Trajectory      
        # #####################################
        from b_ReadGEODYN import read_ascixyz
        trajectory_df_arcs[arc] = read_ascixyz(ascii_xyz_file, geodyn_run_params['YR'] )

        
        if geodyn_run_params['verbose_loading'] == True:
            print('       Trajectory data loaded')
        else:
            pass




        ######################################
        ##       Read Density Values
        ######################################
        from b_ReadGEODYN import read_density_file
        den_arcs[arc] = read_density_file(density_file, geodyn_run_params['YR'] )
        
        
        
        if geodyn_run_params['verbose_loading'] == True:
            print('       Density data loaded')
        else:
            pass



        ######################################
        ##   -   Read Residual Values   -   ##
        ######################################
        from b_ReadGEODYN import read_observed_resids, read_residual_summarybystation, read_resid_measurement_summaries


        resids_observed_arcs[arc] = read_observed_resids(iieout_file, geodyn_run_params['YR'] , geodyn_run_params['DATA_TYPE'])
        resids_summary_station_arcs[arc] = read_residual_summarybystation(iieout_file)
        resids_meas_summary_arcs[arc] = read_resid_measurement_summaries(iieout_file)

        
        
        if geodyn_run_params['verbose_loading'] == True:
            print('       Observation Residuals \n       Summary by Station \n        Measurement Summary data loaded')
        else:
            pass
    
    ######################################
    ##    -   Read IIEOUT STATS    -    ##
    ######################################    
    from b_ReadGEODYN import save_stats_to_dict
    RunStats_arcs[arc] = save_stats_to_dict(iieout_file, geodyn_run_params['den_model'], sat_name, geodyn_run_params['DATA_TYPE'], Verbose_Stats=geodyn_run_params['Verbose_Stats'] )
    
    
    #     ######################################
    #     ##       Return collected Datasets
    #     ######################################
    return(SatMain_AdjustedParams_arcs,
            trajectory_df_arcs,
            den_arcs,
            resids_observed_arcs,
            resids_summary_station_arcs,
            resids_meas_summary_arcs,
            RunStats_arcs)




























In [2]:
%load_ext autoreload
%autoreload 2

# Load multiple arcs:
##################################
# INPUT PARAMETERS:
##################################


arc_list = ['030914_2wk',
            '030928_2wk',
            '031012_2wk',
            '031026_2wk',
            '031109_2wk',
            '031123_2wk',
            '031207_2wk',
#             '031221_2wk',
           ]

geodyn_run_params = {}
geodyn_run_params['arc_list']        = arc_list
geodyn_run_params['sat_file']        = 'st'
geodyn_run_params['SAT_ID']          = 7501001
geodyn_run_params['grav_id']         = 'goco05s' 
geodyn_run_params['den_model']       = 'msis2'
geodyn_run_params['local_path']      = '/data/geodyn_proj/analysis/starlette_analysis/'
geodyn_run_params['AccelStatus']     = 'acceloff'

msis2_model = 'msis2'
path_to_msis2 = ('/data/geodyn_proj/runs_geodyn/results/'+
                 geodyn_run_params['sat_file'] +'/'+
                 geodyn_run_params['den_model']+'/'+  
                 geodyn_run_params['den_model']+'_'+ 
                 geodyn_run_params['AccelStatus'] +'/')

geodyn_run_params['path_to_data']    = path_to_msis2
geodyn_run_params['YR']              = 2003
geodyn_run_params['DATA_TYPE']       = 'SLR'
geodyn_run_params['verbose_loading'] = True
geodyn_run_params['Verbose_Stats']   = False


(SatMain_AdjustedParams_arcs,
trajectory_df_arcs,
den_arcs,
resids_observed_arcs,
resids_summary_station_arcs,
resids_meas_summary_arcs,
RunStats_arcs)  = Read_GEODYN_func_MultipleArcs(geodyn_run_params)   


              Loading /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/st030914_2wk.goco05s

       File exists: iieout 
               /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/IIEOUT/st030914_2wk.goco05s
       File exists: ascii_xyz 
               /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/XYZ_TRAJ/st030914_2wk.goco05s
       File exists: densityfil 
               /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/DENSITY/st030914_2wk.goco05s

       Loading data... 

       Parameter adjustment data loaded
       Trajectory data loaded
       Density data loaded
       Observation Residuals 
       Summary by Station 
        Measurement Summary data loaded
              Loading /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/st030928_2wk.goco05s

       File exists: iieout 
               /data/geodyn_proj/runs_geodyn/results/st/msis2/msis2_acceloff/IIEOUT/st030928_2wk.goco05s
       File exists: ascii_

In [3]:
# initialize plotly:
import plotly.graph_objects as go
import numpy as np
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import plotly.express as px
import datetime


col1 = px.colors.qualitative.Plotly[0]
col2 = px.colors.qualitative.Plotly[1]
col3 = px.colors.qualitative.Plotly[2]

In [116]:
SAT_ID = geodyn_run_params['SAT_ID']
m1 = geodyn_run_params['den_model']
# last_iter = 5
which_stat = 'CURRENT_VALUE' # 2 is the current val


AdjustedParams_m1 = SatMain_AdjustedParams_arcs

# make plot:
fig = make_subplots(
    rows=1, cols=1,)

for i,arc in enumerate(geodyn_run_params['arc_list']):
    i_arc = i+1
    last_iter = list(AdjustedParams_m1[arc].keys())[-1]

    # Organize the x axis dates axis for labeling:
    labels = list(AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'].keys())
#     print(last_iter)
    val_list = []
    for i in AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'].keys():
        val_list.append(AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'][i][which_stat])
    labels = list(AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'].keys())

    
    val_list = []
    for i in AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'].keys():
        val_list.append(AdjustedParams_m1[arc][last_iter][SAT_ID]['0CD'][i][which_stat])
    fig.add_trace(go.Scatter(x=labels,
                                     y=val_list,
                                    name= ' Arc ' +str(i_arc) +' | Iters: '+ str(last_iter),
                                     mode='markers',
                                     marker=dict(
                                     size=7,),
#                                      showlegend=False,
                                     ),
                                     row=1, col=1,
                                     )


# fix layout info:
fig.update_yaxes( title="Cd (Unitless)",exponentformat= 'power',row=1, col=1)
fig.update_xaxes( title="Date", row=1, col=1)
fig.update_layout(title="Time Dependent Drag Coefficient ")
fig.update_layout(
    font=dict(
        size=14,
             ),)
# fig.update_layout(
#     autosize=False,
#     width=600,
#     height=500,)

iplot(fig)







In [5]:
den_arcs.keys()

dict_keys(['030914_2wk', '030928_2wk', '031012_2wk', '031026_2wk', '031109_2wk', '031123_2wk', '031207_2wk'])

In [6]:
data_nums_1 = 1000
data_nums_2 = 100


Density_m1 = den_arcs
fig = make_subplots(rows=1, cols=1, 
        subplot_titles=(["Every 100th point"]),
                       )

for arc in geodyn_run_params['arc_list']:

    fig.add_trace(go.Scatter(x=Density_m1[arc]['Date'][::data_nums_2],
                             y=Density_m1[arc]['rho (kg/m**3)'][::data_nums_2],
                             name = m1 +arc ,
                             mode='markers',
                                marker=dict(color=col1,
                                size=3,
                                ),
                              showlegend=False,
                               ),
                               row=1, col=1,
                               )


fig.update_layout(
    title="Density along Starlette Orbit",
    )
fig.update_yaxes(type="log", exponentformat= 'power',)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_yaxes(title_text="kg/m^3", row=1, col=1)
fig.update_xaxes(title_text="Date", row=1, col=1)
fig.update_layout(legend= {'itemsizing': 'constant'})


fig.update_layout(
    autosize=False,
    width=900,
    height=700,
)
fig.update_layout(
    font=dict(
        size=18,
             ),)

iplot(fig)


In [18]:


fig = make_subplots(rows=1, cols=1, 
        subplot_titles=(["Orbit averaged Density"]),
                       )

for i_arc, arc in enumerate(geodyn_run_params['arc_list']):
    lat = np.asarray(Density_m1[arc]['Lat'])
    time_pd = pd.to_datetime(Density_m1[arc]['Date'])
    i = np.nonzero( lat[1:]*lat[0:-1]  <  np.logical_and(0 , lat[1:] > lat[0:-1] )  )
    i = i[0]

    d_avg = np.zeros(np.size(i))
    height_avg = np.zeros(np.size(i))
    time_avg = []

    d_avg_roll = []
    
    roll_avg_count = 0
    for j in range(np.size(i)-1):
    #     print(j+1)
        d_avg[j] = np.mean(  Density_m1[arc]['rho (kg/m**3)'][   i[j] : i[j+1]-1  ]  )
        height_avg[j] = np.mean(  Density_m1[arc]['Height (meters)'][   i[j] : i[j+1]-1  ]  )
        mean_time=time_pd[   i[j] : i[j+1]-1  ].mean() 
        time_avg.append(  mean_time)

        if roll_avg_count ==2:
            d_avg_roll.append(np.mean([ d_avg[j],  d_avg[j-1]]))
            
            roll_avg_count =0
            
        roll_avg_count+=1

    fig.add_trace(go.Scatter(x=time_avg[::2],
                             y=d_avg_roll,
                            name= ' Arc ' +str(i_arc) ,
                             mode='markers',
                             marker=dict(
                             size=3,),
    #                                      showlegend=False,
                               ),
                               row=1, col=1,
                               )
    

fig.update_layout(
    title="Density along Starlette Orbit",
    )
fig.update_yaxes(type="log", exponentformat= 'power',)
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_yaxes(title_text="kg/m^3", row=1, col=1)
fig.update_xaxes(title_text="Date", row=1, col=1)
fig.update_layout(legend= {'itemsizing': 'constant'})


fig.update_layout(
    autosize=False,
    width=900,
    height=700,
)
fig.update_layout(
    font=dict(
        size=18,
             ),)

iplot(fig)



    

In [91]:
flux_csv = pd.read_csv('noaa_radio_flux.csv', 
                      skiprows = 1 , 
                      names = ['Time', 
                              'sfu'],
                      sep = ',',
                      )

flux_csv['Date'] = pd.to_datetime(flux_csv['Time'], format = '%Y%m%d')
del flux_csv['Time']


flux_starlette = flux_csv[flux_csv["Date"].dt.year==2003][flux_csv["Date"].dt.month>=9]

<ipython-input-91-3a9822075e73>:12: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



In [95]:
ap_csv = pd.read_csv('ap.csv', 
                      skiprows = 1 , 
                      names = ['Time', 
                              'Ap'],
                      sep = ',',
                      )

ap_csv['Date'] = pd.to_datetime(ap_csv['Time'], format = '%Y-%m-%dT%H:%M:%S')
ap_csv

Time  Ap                Date
0    2003-12-17T00:00:00   9 2003-12-17 00:00:00
1    2003-12-17T03:00:00  12 2003-12-17 03:00:00
2    2003-12-17T06:00:00   7 2003-12-17 06:00:00
3    2003-12-17T09:00:00   6 2003-12-17 09:00:00
4    2003-12-17T12:00:00   6 2003-12-17 12:00:00
..                   ...  ..                 ...
108  2003-12-30T12:00:00   5 2003-12-30 12:00:00
109  2003-12-30T15:00:00   5 2003-12-30 15:00:00
110  2003-12-30T18:00:00  15 2003-12-30 18:00:00
111  2003-12-30T21:00:00   9 2003-12-30 21:00:00
112  2003-12-31T00:00:00  15 2003-12-31 00:00:00

[113 rows x 3 columns]

In [114]:
f107a =[]
f107d =[]
date = []
ap = []

import pandas as pd
for i,arc in enumerate(geodyn_run_params['arc_list']):
    print(i,arc)
    msisin_den_file = geodyn_run_params['path_to_data'] + "DENSITY/st"+arc + ".goco05s_msisin"
    DEN1_csv = pd.read_csv(msisin_den_file, 
                        skiprows = 1, 
                        names = ['IYYDDD',
                                 'IYR',
                                  'DAY',
                                 'UTSEC',
                                 'ALTKM',
                                 'GLAT',
                                 'GLON',
                                 'STLOC', 
                                 'AVGFLX',
                                 'FLUX',
                                 'AP1',
                                 'AP2',
                                 'AP3',
                                 'AP4',
                                 'AP5',
                                 'AP6',
                                 'AP7',
                                ],
                        sep = '\s+',
                        )
    DEN1_csv['Date'] = (pd.to_datetime('0'+ ((DEN1_csv['IYR'].astype(int).astype(str))),  format='%y') 
                    +  pd.to_timedelta(DEN1_csv['DAY'], unit='days'))

    f107a.append(DEN1_csv['AVGFLX'].values)
    f107d.append(DEN1_csv['FLUX'].values)
    date.append(DEN1_csv['Date'].values)
    ap.append(DEN1_csv['AP7'].values)

0 030914_2wk
1 030928_2wk
2 031012_2wk
3 031026_2wk
4 031109_2wk
5 031123_2wk
6 031207_2wk


In [115]:

fig = make_subplots(rows=2, cols=1, 
        subplot_titles=(['Ap','F10.7']),
                       )



for i,arc in enumerate(geodyn_run_params['arc_list']):
    i_arc = i+1

    fig.add_trace(go.Scatter(x=pd.to_datetime(date[i][::500]),
                             y=ap[i][::500],
                             name= 'Arc :'+str(i_arc),
                             mode='markers',
                             marker=dict(color = px.colors.qualitative.Plotly[i],
                             size=3,),
                               ),
                               row=1, col=1,
                               )
    fig.add_trace(go.Scatter(x=pd.to_datetime(date[i][::1000]),
                         y=f107d[i][::1000],
#                          name= 'Ap',
                         mode='markers',
                         marker=dict(color = px.colors.qualitative.Plotly[i],
                         size=3,),
                          showlegend=False,

                               ),
                               row=2, col=1,
                               )

fig.update_layout(
    title="Solar and Geomagnetic Activity",
    )

fig.update_yaxes(title_text="nT", row=1, col=1)
fig.update_yaxes(title_text="sfu", row=2, col=1)

fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_layout(legend= {'itemsizing': 'constant'})

fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(
    font=dict(
        size=17,
             ),)

iplot(fig) 

numpy.datetime64('2003-09-28T01:05:48.480000000')

In [9]:
fig = go.Figure()

ResidsObs_m1 = resids_observed_arcs

for i,arc in enumerate(geodyn_run_params['arc_list']):
    i_arc = i+1

    fig.add_trace(go.Scatter(x=ResidsObs_m1[arc]['Date'],
                             y=ResidsObs_m1[arc]['Residual'].values.astype(float),
                             name= 'Arc: '+str(i_arc),
                             mode='markers',
                             marker=dict(
                             size=3,),
#                               showlegend=False,
                             ),
                             )


fig.update_layout(
    title='Observation Residuals',
    yaxis_title="Residuals",
    xaxis_title="Date",
    )
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(
    font=dict(
        size=17,
             ),)

iplot(fig) 

In [10]:
ResidsMeasSumm_m1 = resids_meas_summary_arcs
mark_size = 10

fig = make_subplots(rows=1, cols=1, 
                       )

for i,arc in enumerate(geodyn_run_params['arc_list']):
    i_arc = i+1
    arc_val = arc[:6]
    arc_date = np.datetime64(datetime.datetime.strptime(arc_val, '%y%m%d'))
    iter_index = ResidsMeasSumm_m1[arc]['Iter']==5.0
    mean_arc = ResidsMeasSumm_m1[arc]['MEAN'][iter_index].values.astype(float)
#     rms_arc = ResidsMeasSumm_m1[arc]['RMS'][iter_index].values.astype(float)
    
    fig.add_trace(go.Scatter(x=[arc_date],
                             y=mean_arc,
                             name= 'Arc: '+str(i_arc),
                             mode='markers',
                             marker=dict(
                             size=mark_size,),
#                               showlegend=False,
                             ),
                              row=1, col=1,
                             )
    

    fig.update_layout(
        title="Mean- Residual Measurement Summary",
        )
    fig.update_yaxes(title_text="Residual", row=1, col=1)
#     fig.update_yaxes(title_text="RMS", row=2, col=1)
    fig.update_xaxes(title_text="Arc", row=1, col=1)
#     fig.update_xaxes(title_text="Arc", row=2, col=1)
    fig.update_layout(legend= {'itemsizing': 'constant'})
    fig.update_xaxes(tickangle=0)

    fig.update_layout(
        font=dict(
            size=15,
                 ),)


fig.show()

In [11]:
ResidsMeasSumm_m1 = resids_meas_summary_arcs
mark_size = 10

fig = make_subplots(rows=1, cols=1, 
                       )

for i,arc in enumerate(geodyn_run_params['arc_list']):
    i_arc = i+1

    arc_val = arc[:6]
    arc_date = np.datetime64(datetime.datetime.strptime(arc_val, '%y%m%d'))
    iter_index = ResidsMeasSumm_m1[arc]['Iter']==5.0
    rms_arc = ResidsMeasSumm_m1[arc]['RMS'][iter_index].values.astype(float)
        
    fig.add_trace(go.Scatter(x=[arc_date],
                         y=rms_arc,
                         name= 'Arc: '+str(i_arc),
                         mode='markers',
                         marker=dict(
                         size=mark_size,),
#                               showlegend=False,
                         ),
                          row=1, col=1,
                         )

    fig.update_layout(
        title="RMS- Residual Measurement Summary",
        )
#     fig.update_yaxes(title_text="Residual", row=1, col=1)
    fig.update_yaxes(title_text="RMS", row=1, col=1)
    fig.update_xaxes(title_text="Arc", row=1, col=1)
#     fig.update_xaxes(title_text="Arc", row=2, col=1)
    fig.update_layout(legend= {'itemsizing': 'constant'})
    fig.update_xaxes(tickangle=0)

    fig.update_layout(
        font=dict(
            size=15,
                 ),)


fig.show()

## Compare the Coefficient of Drag

Details:
- the $C_d$ is an adjusted parameter in GEODYN.  Each iteration, it is estimated and adjusted to improve the OD simulation
- $C_d$ is treated as a constant in GEODYN (for any iteration). The factor $C_d$ varies slightly with satellite shape and atmospheric composition. However, for any geodetically useful satellite, it may be treated as a satellite dependent constant.

- $ \bar{A}_D = -\frac{1}{2} C_d \frac{A_s}{m_s} \rho_d v_r \bar{v}_r $
  - $A_D$  acceleration due to atmospheric drag force  
  - $C_d$ is the satellite drag coefficient  
  - $A_s$ is the cross-sectional area of the satellite  
  - $m_s$ is the mass of the satellite  
  - $\rho_d$is the-density of the atmosphere at the satellite position  
  - $\bar{v}_r$  is the velocity vector of the satellite relative to the atmosphere, and  
  - $v_r$  is the magnitude of the velocity vector, vr .  



### Residuals (obervation residuals)
Details:
 - in general, residuals are (observed minus computed)
     - obervation is from the observation file supplied by SLR tracking data
     - computed is what GEODYN is computing the location of the satellite should be
     - 
     


## Density Output Analysis

Details:
- the density is sampled from the models along the orbit of the Starlette satellite





## DRHODZ
